In [40]:
from pymongo import MongoClient
import pandas as pd
import json as js
import folium

# Calling from mongo

It is a problem to have many companies with multiple office locations. I (we) solved that using "unwind", and "match" to link the whole query

In [41]:
def connectCollection(database, collection):
    client = MongoClient()
    db = client[database]
    coll = db[collection]
    return db, coll

db, coll = connectCollection('companies','companies')
pipeline = [
    { "$unwind": "$offices"},
    {"$match":{ "$and": [  {"founded_year":{"$gt":2000}},
            {"funding_rounds.raised_amount":{"$gt":1000000}}, { "$or":[{"category_code":"web"},
            {"category_code":"software"},{"category_code":"games_video"},
            {"category_code":"hardware"},{"category_code":"mobile"},{"category_code":"music"},
            {"category_code":"photo_video"},{"category_code":"design"}]}] }}
#    {"$match":"}
    ]
results = list(coll.aggregate(pipeline))

i had problems of unknown nature. I had a beautiful way to extract long and latitude in a a list to implement in folium, but now that is gone and i had to make up a patch 

In [42]:
location_raw=[]
name=[]
lon=[]
lat=[]

for element in results:
    name.append(element["name"])
    for coord in element["offices"].items():
        
        #print(coord)
        
        if coord[0]=="longitude":
            lon.append(coord[1])
        elif coord[0]=="latitude":
            lat.append(coord[1])

In [43]:
# to check 
print(len(name),len(lat),len(lon))

1591 1591 1591


# Creating my dataframe

In [44]:
l={"name":name, "longitude":lon, "latitude":lat}
data_locations=pd.DataFrame(data=l)

In [45]:
data_clean=data_locations.dropna()

# Creating lists to insert in folium with coordinates and names

In [46]:
office_lat=list(data_clean["latitude"])
office_long=list(data_clean["longitude"])
office_name=list(data_clean["name"])

# Calling ubication of airports

In [47]:
%store
%store -r

Stored variables and their in-db values:
facilities              -> ['airport', 'airport', 'airport', 'airport', 'airp
lat_airport             -> ['l', 'a', 't', 'i', 't', 'u', 'd', 'e']
lon_airport             -> ['l', 'o', 'n', 'g', 'i', 't', 'u', 'd', 'e']


# Folium

In [28]:
world_map=folium.Map(location=[52.5200,13.4050], zoom_start=12)

Offices

In [31]:
for i in range(len(office_lat)):
    folium.Marker([office_lat[i],office_long[i]],
                    radius=2,
                    icon=folium.Icon(icon='cloud',color='red'),
                  popup=office_name[i]
                   ).add_to(world_map)

Airports

In [48]:
for i in range(len(facilities)):
    folium.Marker([lat_airport[i],lon_airport[i]],
                 radius=2,
                 icon=folium.Icon(icon='cloud',color='blue'),
                 popup=facilities[i]).add_to(world_map)

ValueError: Location should consist of two numerical values, but 'l' of type <class 'str'> is not convertible to float.

In [32]:
world_map

In [34]:
l={"name":name, "location":location_list}
data_locations=pd.DataFrame(data=l)

In [35]:
data_locations

name                                           location
0             Facebook  {'type': 'Point', 'coordinates': [-122.151801,...
1             Facebook  {'type': 'Point', 'coordinates': [-6.267494, 5...
2             Facebook  {'type': 'Point', 'coordinates': [-73.9792469,...
3              Twitter  {'type': 'Point', 'coordinates': [-122.4169244...
4              AddThis  {'type': 'Point', 'coordinates': [-77.245195, ...
..                 ...                                                ...
535        FleetMatics     {'type': 'Point', 'coordinates': [None, None]}
536        FleetMatics     {'type': 'Point', 'coordinates': [None, None]}
537             800APP     {'type': 'Point', 'coordinates': [None, None]}
538          InfoLogix  {'type': 'Point', 'coordinates': [-75.1069232,...
539  OfficialVirtualDJ     {'type': 'Point', 'coordinates': [None, None]}

[540 rows x 2 columns]

In [43]:
world_map=folium.Map(location=[52.5200,13.4050], zoom_start=12)
for company in data_locations:
world_map

In [50]:
#si quiero añadir información a la colección $set (para el geoindex)
for place in rest:
    value = {"$set": {'location':getLocation(place)}}
    coll.update_one(place,value)

In [51]:
# eliminar las antiguas coordenadas
for place in rest:
    value = {"$unset": {'offices.latitude':''}}
    value = {"$unset": {'offices.longitude':''}}
    coll.update_one(place,value)
    # <collection>.update_one(<document>,<value>)

In [54]:
'''
prefered_city = coll.find(
    {"location":
     {"$near":
      {"$geometry":
       {"type":"Point",
        "coordinates":[-73.9712,40.7831]
       },
       "$maxDistance":10000
      }
     }
    }
)
prefered_city=list(prefered_city)
'''

'\nprefered_city = coll.find(\n    {"location":\n     {"$near":\n      {"$geometry":\n       {"type":"Point",\n        "coordinates":[-73.9712,40.7831]\n       },\n       "$maxDistance":10000\n      }\n     }\n    }\n)\nprefered_city=list(prefered_city)\n'

In [58]:
map_city=folium.Map(location=[40.7221,-73.9712], zoom_start=12)
map_city
'''
for wendy in manhattanWendys:
    folium.Marker(wendy['location']['coordinates'][::-1],
                    radius=2,
                    icon=folium.Icon(icon='cloud',color='red'), 
                   ).add_to(map_city)
    
for wendy in manhattanWendys[:5]:
    folium.Marker(wendy['location']['coordinates'][::-1],
                    radius=2,
                    icon=folium.Icon(icon='cloud',color='blue'), 
                   ).add_to(map_city)
'''

"\nfor wendy in manhattanWendys:\n    folium.Marker(wendy['location']['coordinates'][::-1],\n                    radius=2,\n                    icon=folium.Icon(icon='cloud',color='red'), \n                   ).add_to(map_city)\n    \nfor wendy in manhattanWendys[:5]:\n    folium.Marker(wendy['location']['coordinates'][::-1],\n                    radius=2,\n                    icon=folium.Icon(icon='cloud',color='blue'), \n                   ).add_to(map_city)\n"